In [1]:
import os
# os.system('pip install einops')
# os.system('pip install pytorch_metric_learning')
import argparse, os, copy, random, sys
import itertools
import pandas as pd
from models.tinyhar import tinyhar
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3' 
os.environ['TF_ENABLE_ONEDNN_OPTS'] = '0'
import warnings
warnings.filterwarnings("ignore", message="To copy construct from a tensor")
warnings.filterwarnings("ignore", category=UserWarning)
import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from sklearn.cluster import AffinityPropagation
from sklearn.mixture import GaussianMixture
from functools import partial
from tqdm import *
import dataset, utils_CGCD, losses, net
from net.resnet import *
from models.modelgen import ModelGen, ModelGen_new
# from torchsummary import summary
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
import json
from infoNCE import InfoNCE
from utils_CGCD import calculate_accuracy
import os
from collections import Counter
import multiprocessing
import logging
import pandas as pd
device = 'cuda' if torch.cuda.is_available() else 'cpu'



class MyDict(dict):
    def __init__(self, args):
        self.args

class BlankClass:
    pass

args = BlankClass()

args.dataset = 'realworld'
args.sz_embedding = 1024
args.sz_batch  = 256
args.nb_epochs = 1
args.nb_workers = 4
args.model = "tinyhar"
args.loss = "Proxy_Anchor"
args.optimizer = "adamw"
args.lr = 1e-3 
args.weight_decay = 1e-7
args.lr_decay_step = 5
args.lr_decay_gamma =  0.5
args.alpha = 16
args.mrg = 0.4
args.warm = 5
args.bn_freeze = True
args.use_wandb = False
args.contrastive_loss_type  = "Online_Finetuning_NCE"
args.only_test_step1 = True
args.only_test_step2 = True
args.standarization_prerun = False
args.standarization_run_time = False
args.learnable_loss_weights = True
args.log_results = False
args.kd_weight = 10
args. pa_weight = 1
args.l2_norm =  True
args.use_split_modlue =  True
args.use_GM_clustering =  True
args.exp = '0'

In [2]:
lrs = [1e-4]
kd_weights = [100] #[1,5,10, 15, 20]
pa_wights = [20] #[1, 5, 10, 15, 20]
contrastive_weights = [20]#[1,10]
folds =[1] #[0,1,2,3,4] #[0,1,2,3,4] #[0,1,2,3,4] #[0,1,2,3,4] #[0,1,2,3,4]#[0,1,2,3,4] #[1,2,3,4,5]  #[1,2,3,4,5]

results_df = pd.DataFrame(columns = ['Dataset', 'Iteration', 'Initial Acc', 'Initial F1', 'Incremental Acc Seen1',  'Incremental F1 Seen1', 'Incremental Acc Seen2',  'Incremental F1 Seen2', 'Incremental Acc Unseen', 'Incremental F1 Unseen', 'Incremental Acc All', 'Incremental F1 All', "Forget Acc", 'Forget F1' ])

root_dir = f'{os.getcwd()}' #/continual_learning'


pth_rst_exp_step_1 = f'{root_dir}/Saved_Models/Initial/{args.contrastive_loss_type}/' + args.dataset + '/' # + args.model + '_sp_' + str(args.use_split_modlue) + '_gm_' + str(args.use_GM_clustering) + '_' + args.exp
pth_rst_exp_log_step_1 = pth_rst_exp_step_1+f'results_{args.dataset}_{args.model}.log'

os.makedirs(pth_rst_exp_step_1, exist_ok=True)

pth_rst_exp_step_2 = f'{root_dir}/Saved_Models/Incremental/{args.contrastive_loss_type}/' + args.dataset + '/'
pth_rst_exp_log_step_2 = pth_rst_exp_step_2  + f"results_{args.dataset}_{args.model}.log"
os.makedirs(pth_rst_exp_step_2, exist_ok=True)

if(args.log_results):
    logger_1 = logging.getLogger('logger_1')
    logger_1.setLevel(logging.INFO)
    file_handler_1 = logging.FileHandler(pth_rst_exp_log_step_1, mode='w')
    # file_handler_1.setFormatter(logging.Formatter('%(asctime)s - %(message)s'))
    logger_1.addHandler(file_handler_1)

    # Configure the second logger for 'experiment_results_step_2.log'
    logger_2 = logging.getLogger('logger_2')
    logger_2.setLevel(logging.INFO)
    file_handler_2 = logging.FileHandler(pth_rst_exp_log_step_2, mode='w')
    # file_handler_2.setFormatter(logging.Formatter('%(asctime)s - %(message)s'))
    logger_2.addHandler(file_handler_2)

    logger_1.info(f"\n******** Dataset: {args.dataset}, Standardize: True, Model: {args.model} ******** \n")
    logger_2.info(f"\n******** Dataset: {args.dataset}, Standardize: True, Model: {args.model} ******** \n")


os.makedirs(pth_rst_exp_step_2, exist_ok= True)
stage_1_test_accs_seen, stage_1_test_f1s_seen, stage_2_test_accs_seen, stage_2_test_f1s_seen= [], [], [], []
stage_2_val_accs_seen, stage_2_val_accs_unseen, stage_2_val_accs_overall   = [], [], []
test_accs_seen, test_accs_unseen, test_accs_overall   = [], [], []
test_f1s_seen, test_f1s_unseen, test_f1s_overall   = [], [], []

In [3]:
print("Using device", device)
print("Model :", args.contrastive_loss_type)
print("Architecture :", args.model)
print("Contrastive Loss Type :", )

lr = 1e-4
kd_weight = 100
pa_weight = 20
contrastive_weight = 20
fold = 0

print(contrastive_weights,pa_wights,kd_weights)

torch.cuda.manual_seed(42)
np.random.seed(42)
torch.manual_seed(42)
torch.backends.cudnn.deterministic = True
torch.backends.cudnn.benchmark = False

fold_style_print_log = f"\n******************Fold: {fold} ******************************\n"


print(fold_style_print_log)

if(args.log_results):    
    logger_1.info(fold_style_print_log)
    logger_2.info(fold_style_print_log)   

args.lr = lr
args.weight_decay =  args.lr
args.kd_weight  = kd_weight
args.pa_weight = pa_weight
args.contrastive_weight = contrastive_weight


print("Dataset :", args.dataset)
if args.dataset =='wisdm':
    pth_dataset = f'{root_dir}/HAR_data/Wisdm/'
    window_len = 40
    n_channels = 3
elif args.dataset =='realworld':
    pth_dataset = f'{root_dir}/HAR_data/realworld/'
    nb_classes_now = 8
    window_len = 100
    n_channels = 3
elif args.dataset =='oppo':
    pth_dataset = f'{root_dir}/HAR_data/oppo/'
elif args.dataset =='pamap':
    pth_dataset = f'{root_dir}/HAR_data/pamap/'
    nb_classes_now = 12
    window_len = 200
    n_channels = 9
elif args.dataset =='mhealth':
    pth_dataset = f'{root_dir}/HAR_data/mhealth/'
    nb_classes_now = 6
    window_len = 100
    n_channels = 9

if(args.use_wandb):
    import wandb
    wandb.init(
        # set the wandb project where this run will be logged
        project="CGCD-HAR-Supervised_NCE",
        name='specific-run-name',
        resume='allow',
        # track hyperparameters and run metadata
        config={
        "learning_rate_step_1": args.lr,
        "learning_rate_step_2": args.lr,
        "sz_embedding" : args.sz_embedding,
        "window_len": window_len,
        "batch-size" : args.sz_batch,
        "loss" : args.loss,
        "nb_workers": args.nb_workers,
        "architecture": args.model,
        "dataset": args.dataset,
        "epochs": args.nb_epochs,
        "optimizer" : args.optimizer, 
        "weight-decay" :args.weight_decay,
        "lr-decay-step" : args.lr_decay_step,
        "lr-decay-gamma" : args.lr_decay_gamma,
        "alpha" : args.alpha,
        "mrg" : args.mrg,
        "warm" : args.warm,
        "bn-freeze" : args.bn_freeze,
        "l2-norm" : args.l2_norm,
        "exp" : args.exp,
        "KD_weight" : args.kd_weight,
        "pa_weight" : args.pa_weight,
        'contrastive_weight' : contrastive_weight

        }
    ) 
    wandb.log({"Method": args.contrastive_loss_type})

# Set the dimensionality reduction method to t-SNE for later visualization or processing
dim_reduction_method = "tsne"         

# Initializing Dataloaders for training, evaluation, and testing datasets
print("Setting up Dataloaders..")

# Load the training dataset with the first fold and standardization parameters
dset_tr_0 = dataset.load(name=args.dataset, root=pth_dataset, mode='train_0', windowlen=window_len, 
                        autoencoderType=None, standardize=args.standarization_prerun, fold=fold)

# Calculate the mean and standard deviation of the training dataset for Standardization
mean = np.mean(dset_tr_0.xs, axis=0)
std = np.std(dset_tr_0.xs, axis=0)



# Standardize the training dataset (z-score normalization)
if(args.standarization_run_time):
    dset_tr_0.xs = (dset_tr_0.xs - mean) / (std + 1e-5)  # Adding a small value to prevent division by zero

# Create the dataloader for the training dataset with batch shuffling
dlod_tr_0 = torch.utils.data.DataLoader(dset_tr_0, batch_size=args.sz_batch, shuffle=True, 
                                        num_workers=args.nb_workers, pin_memory=True, 
                                        worker_init_fn=lambda x: np.random.seed(42))

# Load the evaluation dataset using the same mean and std as the training dataset
dset_ev = dataset.load(name=args.dataset, root=pth_dataset, mode='eval_0', windowlen=window_len, 
                    autoencoderType=None, standardize=args.standarization_prerun, fold=fold)

# Normalize the evaluation dataset using the training set statistics

if(args.standarization_run_time):dset_ev.xs = (dset_ev.xs - mean) / (std + 1e-5)

# Create the dataloader for the evaluation dataset (no shuffling)
dlod_ev = torch.utils.data.DataLoader(dset_ev, batch_size=args.sz_batch, shuffle=False, 
                                    num_workers=args.nb_workers, pin_memory=True, 
                                    worker_init_fn=lambda x: np.random.seed(42))

# Load the test dataset and normalize using the training set statistics
dset_test_0 = dataset.load(name=args.dataset, root=pth_dataset, mode='test_0', windowlen=window_len, 
                        autoencoderType=None, standardize=args.standarization_prerun, fold=fold)

# Normalize the test dataset
if(args.standarization_run_time): dset_test_0.xs = (dset_test_0.xs - mean) / (std + 1e-5)

# Create the dataloader for the test dataset (no shuffling)
dlod_test_0 = torch.utils.data.DataLoader(dset_test_0, batch_size=args.sz_batch, shuffle=False, 
                                        num_workers=args.nb_workers, pin_memory=True, 
                                        worker_init_fn=lambda x: np.random.seed(42))

# Set the number of classes for classification tasks
print("Initial Step \n")
nb_classes = dset_tr_0.nb_classes()
nb_subjects = dset_tr_0.nb_subjects()
print("\n")
# Configuration for different model architectures
if(args.model == 'resnet18'):
    # Setting up configuration for ResNet18 model
    cfg = {'weights_path': 'CGCD-main/src/Saved_Models/UK_BioBank_pretrained/mtl_best.mdl', 
        'use_ssl_weights': False, 'conv_freeze': False, 'load_finetuned_mtl': False,
        'checkpoint_name': '', 'epoch_len': 2, 'output_size': nb_classes, 
        'embedding_dim': args.sz_embedding, 'bottleneck_dim': None,
        'weight_norm_dim': '', 'n_channels': n_channels, 'window_len': window_len}

    # Create the ResNet18 model
    model = ModelGen_new(cfg).create_model().to(device)

elif(args.model == 'tinyhar'):
    # Create the tinyHAR model
    model = tinyhar(n_channels, window_len, args.sz_embedding).to(device)

elif(args.model == 'harnet'):
    # Load a pretrained HARNet model from the torch hub and modify its architecture
    repo = 'OxWearables/ssl-wearables'
    model = torch.hub.load(repo, 'harnet5', class_num=nb_classes, pretrained=True).to(device)
    
    # Remove the classifier and add a new embedding layer
    del model.classifier
    model.embedding = nn.Sequential(nn.Linear(model.feature_extractor.layer5[0].out_channels, 
                                            args.sz_embedding)).to(device)

# Count and print the total number of parameters in the model
total_params = sum(p.numel() for p in model.parameters())
print(f"Model Name: {args.model}, Total Parameters: {total_params}")

# Initialize Proxy Anchor Loss for metric learning
criterion_pa = losses.Proxy_Anchor(nb_classes=nb_classes, sz_embed=args.sz_embedding, 
                                mrg=args.mrg, alpha=args.alpha).to(device)

# GPU settings for training
gpu_id = 0

# Define training parameter groups depending on the model
if(args.model == 'tinyhar'):
    # Freeze batch normalization layers for tinyHAR model
    args.bn_freeze = False
    args.warm = 0
    
    # Set different learning rates for the prediction head and the rest of the model
    param_groups = [
        {'params': list(set(model.model.parameters()).difference(set(model.model.prediction.parameters()))) 
        if gpu_id != -1 else list(set(model.module.parameters()).difference(set(model.module.model.prediction.parameters())))},
        {'params': model.model.prediction.parameters() 
        if gpu_id != -1 else model.model.prediction.parameters(), 'lr': float(args.lr) * 1},
    ]
else:
    # Define parameter groups for other models with different learning rates for the embedding layer
    param_groups = [
        {'params': list(set(model.parameters()).difference(set(model.embedding.parameters()))) 
        if gpu_id != -1 else list(set(model.module.parameters()).difference(set(model.module.model.embedding.parameters())))},
        {'params': model.embedding.parameters() 
        if gpu_id != -1 else model.embedding.parameters(), 'lr': float(args.lr) * 1},
    ]

for layer in model.children():
    if hasattr(layer, 'reset_parameters'):
        layer.reset_parameters()


# Add the Proxy Anchor loss parameters with a higher learning rate
param_groups.append({'params': criterion_pa.parameters(), 'lr': float(args.lr) * 100})

# Initialize the AdamW optimizer with weight decay
opt_pa = torch.optim.AdamW(param_groups, lr=float(args.lr), weight_decay=args.weight_decay)

# Optionally, a learning rate scheduler can be added (commented out)
# scheduler_pa = torch.optim.lr_scheduler.StepLR(opt_pa, step_size=args.lr_decay_step, gamma=args.lr_decay_gamma)


    # print('Training parameters: {}'.format(vars(args)))
# Print the training parameters and the total number of epochs for the current training run.
print('Training for {} epochs'.format(args.nb_epochs))
losses_list = []
best_recall = [0]
best_epoch = 0
best_acc, es_count = 0, 0  # Initialize best accuracy and early stopping count.

version = 1
step = 1

# Initialize the InfoNCE loss function for contrastive learning with a specified temperature.
nce_loss = InfoNCE(temperature=0.07, negative_mode='paired')

# Define weights for the Proxy Anchor loss and contrastive loss.
l_pa_weight = torch.tensor(1.0, requires_grad=True)
l_contrastive_weight = torch.tensor(1.0, requires_grad=True)

# Initial Validation Lossesi
if(args.only_test_step1 == False):
    first_validation_losses = losses.get_validation_losses_step_1(model, criterion_pa, nb_classes, args, nce_loss, dlod_ev)
    validation_losses = first_validation_losses
# Start the training loop for the specified number of epochs.
for epoch in range(0, args.nb_epochs):
    # Skip training if only testing is required.
    if args.only_test_step1: continue
    
    # Set the model to training mode.
    model.train()

    # If batch normalization freezing is enabled, set all BatchNorm layers to evaluation mode.
    # This prevents the update of batch normalization statistics during training.
    if args.bn_freeze:
        modules = model.modules() if gpu_id != -1 else model.module.model.modules()
        for m in modules:
            if isinstance(m, nn.BatchNorm2d):
                m.eval()

    # Warmup strategy: freeze certain layers in the initial epochs and gradually unfreeze them.
    if args.warm > 0:
        if gpu_id != -1:
            if args.model == 'tinyhar':
                # Unfreeze the prediction layers and criterion for the 'tinyhar' model.
                unfreeze_model_param = list(model.model.prediction.parameters()) + list(criterion_pa.parameters())
            else:
                # Unfreeze the embedding layers and criterion for other models.
                unfreeze_model_param = list(model.embedding.parameters()) + list(criterion_pa.parameters())
        else:
            if args.model == 'tinyhar':
                unfreeze_model_param = list(model.model.prediction.parameters()) + list(criterion_pa.parameters())
            else:
                unfreeze_model_param = list(model.embedding.parameters()) + list(criterion_pa.parameters())

        # Freeze all layers except the specified parameters during warmup.
        if epoch == 0:
            for param in list(set(model.parameters()).difference(set(unfreeze_model_param))):
                param.requires_grad = False
        
        # Unfreeze the layers after the warmup period is over.
        if epoch == args.warm:
            for param in list(set(model.parameters()).difference(set(unfreeze_model_param))):
                param.requires_grad = True

    total, correct = 0, 0
    total_train_loss = 0
    total_data = 0
    total_pa_loss = 0
    total_contrastive_loss = 0

    # Iterate over the training data (features x, labels y, and other data z).
    for batch_idx, (x, y, z) in enumerate(dlod_tr_0):

        # Forward pass: extract features from the model.
        feats = model(x.squeeze().to(device))

        # Extract positive proxies for the given labels y.
        positive_proxies = criterion_pa.proxies[[torch.tensor(y, dtype=torch.long)]]

        # Collect negative proxies for all labels except the current label.
        negetive_proxies = []
        for y_temp in y:
            t = [i for i in range(nb_classes) if i != y_temp.item()]  # All other proxies are negative.
            if len(negetive_proxies) == 0:
                negetive_proxies = criterion_pa.proxies[t].unsqueeze(0)
            else:
                negetive_proxies = torch.concat((negetive_proxies, criterion_pa.proxies[t].unsqueeze(0)))

        # Compute Proxy Anchor loss.
        loss_pa = criterion_pa(feats, y.squeeze().to(device)).to(device)

        # Compute contrastive loss between the extracted features and proxies.
        # contrastive_loss = utils_CGCD.contrastive_loss(feats, y, criterion_pa.proxies, True).to(device)

        # If contrastive loss type is NCE (Noise Contrastive Estimation), compute the NCE loss.
        if args.contrastive_loss_type in ['G-Baseline_NCE', 'Offline_NCE', 'Online_Finetuning_NCE', 'G-Baseline_NCE_WFR']:
            contrastive_loss = nce_loss(feats, positive_proxies, negetive_proxies)
        # If contrastive loss type is the baseline contrastive loss, compute the corresponding loss.
        elif args.contrastive_loss_type == 'G-Baseline_Contrastive':
            contrastive_loss = utils_CGCD.contrastive_loss(feats, y, criterion_pa.proxies, True).to(device)
        # If no contrastive loss is required, set contrastive loss to zero.
        else:
            contrastive_loss = torch.tensor(0).to(device)
            # model.contrastive_weight_lr.requires_grad = False

        # Combine the Proxy Anchor loss and contrastive loss with their respective weights.
        # print(validation_losses)#
        # Only Offline and Online Finetuning Models donot have contrastive losses.
        if(args.contrastive_loss_type not in ['Offline', 'Online_Finetuning', 'G-Baseline']):
            training_losses = [loss_pa.item(), contrastive_loss.item()]
            max_ratio = max([validation_losses[i]/training_losses[i] for i in range(len(validation_losses))])

            weights = [(validation_losses[i]/training_losses[i])/first_validation_losses[i] for i in range(len(validation_losses))]

            normalized_weights = [weights[i]/min(weights) for i in range(len(weights))]
            total_loss =  weights[0]*loss_pa + weights[1]*contrastive_loss
        else:
            total_loss = loss_pa
        # Zero the gradients before performing backpropagation.
        opt_pa.zero_grad()

        # Perform backpropagation to compute the gradients.
        total_loss.backward()

        # Clip gradients to prevent exploding gradients.
        torch.nn.utils.clip_grad_value_(model.parameters(), 10)
        if args.loss == 'Proxy_Anchor':
            torch.nn.utils.clip_grad_value_(criterion_pa.parameters(), 10)

        # Perform an optimization step to update the model parameters.
        opt_pa.step()

        # Accumulate the total loss for reporting.
        total_pa_loss += loss_pa.item() * x.size(0)
        total_contrastive_loss += contrastive_loss.item() * x.size(0)
        total_train_loss += total_loss.item() * x.size(0)
        total_data += x.size(0)

        # Print the progress of the training epoch.
        print("Train Epoch: {} [{}/{} ({:.0f}%)] Loss: {:.4f}/{:.4f} Acc: {:.4f}".format(epoch, batch_idx + 1, len(dlod_tr_0), 100. * batch_idx / len(dlod_tr_0), total_loss.item(), 0, 0), end="\r")

    # Print the total contrastive loss, Proxy Anchor loss, and overall loss after the epoch.
    print("Contrastive Loss {:.4f}, PA Loss {:.4f}, Total Loss {:.4f}".format(total_contrastive_loss / total_data, total_pa_loss / total_data, total_train_loss / total_data))

    validation_losses = losses.get_validation_losses_step_1(model, criterion_pa, nb_classes, args, nce_loss, dlod_ev)
    # exit()
    # Evaluate the model using cosine similarity with proxies.
    with torch.no_grad():
        feats, _ = utils_CGCD.evaluate_cos_(model, dlod_ev)
        cos_sim = F.linear(losses.l2_norm(feats), losses.l2_norm(criterion_pa.proxies))
        _, preds_lb = torch.max(cos_sim, dim=1)
        preds = preds_lb.detach().cpu().numpy()
        # acc_0, _ = utils_CGCD._hungarian_match_(np.array(dlod_ev.dataset.ys), preds)
        acc_0 = accuracy_score(np.array(dlod_ev.dataset.ys), preds)
        print('Valid Epoch: {} Acc: {:.4f}'.format(str(-1), acc_0))
        if args.use_wandb:
            wandb.log({"Step 1: Val Accuracy": acc_0, "custom_step": epoch})
            wandb.log({"Step 1: F1 Score": f1_score(np.array(dlod_ev.dataset.ys), preds, average='macro'), "custom_step": epoch})

    # Save the model if it achieves a new best accuracy.
    if best_acc < acc_0:
        print("Got better model with from accuracy {:.4f} to {:.4f}".format(best_acc, acc_0))
        best_acc = acc_0
        torch.save({'model_pa_state_dict': model.state_dict(), 'proxies_param': criterion_pa.proxies},
                '{}{}_{}_best_windowlen_{}_embedding_size_{}_alpha{}_mrg_{}_version_{}_step_{}_fold_{}.pth'.format(
                    pth_rst_exp_step_1, args.dataset, args.model, window_len, args.sz_embedding, args.alpha, args.mrg, version, step, fold))
        es_count = 0
    else:
        # Increase the early stopping counter if no improvement in accuracy is found.
        es_count += 1
        if epoch > args.warm:
            print("Early stopping count {}".format(es_count))

    # Reset early stopping counter during the warmup period.
    if epoch < args.warm:
        es_count = 0

    # Stop training early if the early stopping counter reaches 10 or if the accuracy is perfect (1.0).
    if es_count == 10 or int(acc_0) == 1:
        print("Early Stopping with Count {} and Best Accuracy {:.4f}".format(es_count, best_acc))
        break

    del total_loss, feats


        #################################################################
        # Proxy Anchor training is now complete.                        #
        #################################################################

# Load the best model checkpoint for further evaluation or fine-tuning.
print('==> Resuming from checkpoint..')
pth_pth = '{}{}_{}_best_windowlen_{}_embedding_size_{}_alpha{}_mrg_{}_version_{}_step_{}_fold_{}.pth'.format(
    pth_rst_exp_step_1, args.dataset, args.model, window_len, args.sz_embedding, args.alpha, args.mrg, version, step, fold)
checkpoint = torch.load(pth_pth, map_location=torch.device(device))

# Load the model and proxies from the checkpoint.
model.load_state_dict(checkpoint['model_pa_state_dict'])
criterion_pa.proxies = checkpoint['proxies_param']

# Move the model to the specified device and set it to evaluation mode.
model = model.to(device)
model.eval()


Using device cpu
Model : Online_Finetuning_NCE
Architecture : tinyhar
Contrastive Loss Type :
[20] [20] [100]

******************Fold: 0 ******************************

Dataset : realworld
Setting up Dataloaders..


Initial Step 

Classes:  {np.int64(0), np.int64(1), np.int64(2), np.int64(3), np.int64(4), np.int64(5)}
Subjects:  {np.str_('imu\\12'), np.str_('imu\\14'), np.str_('imu\\11'), np.str_('imu\\15'), np.str_('imu\\10'), np.str_('imu\\13')}


Model Name: tinyhar, Total Parameters: 808926
Training for 1 epochs
==> Resuming from checkpoint..


/tmp/ipykernel_2184089/1840579052.py:417: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(pth_pth, map_location=torch.device(device))


tinyhar(
  (model): TinyHAR_Model(
    (layers_conv): ModuleList(
      (0): Sequential(
        (0): Conv2d(1, 100, kernel_size=(5, 1), stride=(1, 1))
        (1): ReLU(inplace=True)
      )
      (1): Sequential(
        (0): Conv2d(100, 100, kernel_size=(5, 1), stride=(2, 1))
        (1): ReLU(inplace=True)
      )
      (2): Sequential(
        (0): Conv2d(100, 100, kernel_size=(5, 1), stride=(1, 1))
        (1): ReLU(inplace=True)
      )
      (3): Sequential(
        (0): Conv2d(100, 100, kernel_size=(5, 1), stride=(2, 1))
        (1): ReLU(inplace=True)
      )
    )
    (channel_interaction): SelfAttention_interaction(
      (query): Linear(in_features=100, out_features=100, bias=False)
      (key): Linear(in_features=100, out_features=100, bias=False)
      (value): Linear(in_features=100, out_features=100, bias=False)
    )
    (channel_fusion): FC(
      (fc): Linear(in_features=300, out_features=200, bias=True)
    )
    (activation): ReLU()
    (temporal_interaction): tem

In [4]:
import numpy as np
import plotly.graph_objects as go
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from sklearn.cluster import KMeans
from collections import Counter
from sklearn.metrics import accuracy_score

In [5]:
feats, ys_ = utils_CGCD.evaluate_cos_(model, dlod_tr_0)

In [6]:
def get_ellipse_points(mean, cov, scale=1.5, n_points=100, n_samples =100):
    
    cov += np.eye(cov.shape[0]) * 1e-6
    dimension = len(mean)
    t = np.linspace(0, 2 * np.pi, n_points)
    circle = np.stack((np.cos(t), np.sin(t)))
    eigvals, eigvecs = np.linalg.eigh(cov)
    transform = eigvecs @ np.diag(np.sqrt(eigvals)*scale)
    
    if(dimension==2):
        ellipse = transform @ circle

        angles = np.random.uniform(0, 2 * np.pi, n_samples)
        radii = np.sqrt(np.random.uniform(0, 1, n_samples))  # Square root ensures uniform sampling in a circle
        unit_circle_points = np.stack((radii * np.cos(angles), radii * np.sin(angles)), axis=1)
    
    # Transform points to fit the ellipse
        ellipse_points = unit_circle_points @ transform.T + mean
    
    
        return ellipse.T + mean, ellipse_points
    
    else:
        
        unit_sphere = np.random.normal(size=(n_samples, dimension))
        unit_sphere /= np.linalg.norm(unit_sphere, axis=1, keepdims=True)  # Normalize to sphere
        radii = np.random.uniform(0, 1, n_samples) ** (1 / dimension)      # Uniform distribution in n-sphere
        
        unit_sphere *= radii[:, None]
        
        # Transform points to fit the n-dimensional ellipse
        ellipse_points = unit_sphere @ transform.T + mean
        return None, ellipse_points

In [7]:
# Assuming 'feats', 'ys', 'proxies', and 'classes' are defined as in your original code
# method = 'tsne'
method = 'pca'
# with torch.no_grad():
#     feats, ys = utils_CGCD.evaluate_cos_(model, dlod_test_0)

samples_each_class = 500

# Perform dimensionality reduction
if method == 'pca':
    pca = PCA(n_components=20, random_state=42)
    pca.fit(feats)
    feats_transformed = pca.transform(feats)
    embedded_data = pca.transform(criterion_pa.proxies.to('cpu').detach().numpy())
    

# elif method == 'tsne':
   
#     # expler_s = torch.full((1024,), 0)
#     # feats_sp = torch.normal(criterion_pa.proxies[y_sp], expler_s).to(device)
#     # feats_sp = losses.l2_norm(criterion_pa.proxies[y_sp])
#     # features_sp = np.array(x_sampled)

#     tsne = TSNE(n_components=2, random_state=42)
#     original_len_feats = len(feats)
#     feats = np.concatenate((feats.to('cpu').detach().numpy(), features_sp,  criterion_pa.proxies.to('cpu').detach().numpy()))
#     feats_transformed = tsne.fit_transform(feats)
#     embedded_data = feats_transformed[-nb_classes:]
#     feats_sp_transformed = feats_transformed[original_len_feats:original_len_feats+ len(features_sp)]
#     feats_transformed = feats_transformed[:original_len_feats]
    

In [8]:
feats

tensor([[ 0.0031, -0.0324, -0.0699,  ...,  0.0289,  0.0177, -0.0083],
        [ 0.0116, -0.0079, -0.0110,  ...,  0.0069,  0.0127,  0.0173],
        [-0.0003, -0.0031, -0.0115,  ...,  0.0061,  0.0069,  0.0155],
        ...,
        [-0.0177,  0.0287, -0.0098,  ...,  0.0522,  0.0027,  0.0375],
        [ 0.0003, -0.0349, -0.0754,  ...,  0.0259,  0.0133, -0.0052],
        [-0.0208, -0.0048, -0.0052,  ..., -0.0587, -0.0160, -0.0431]])

In [9]:
pca.inverse_transform(feats_transformed)

array([[-0.00047152, -0.03459726, -0.07291565, ...,  0.0274234 ,
         0.01465901, -0.00638837],
       [ 0.01123178, -0.00406727, -0.01365959, ...,  0.00758788,
         0.01400919,  0.01448376],
       [ 0.00518235, -0.00442706, -0.01295674, ...,  0.00632534,
         0.00964286,  0.01434213],
       ...,
       [-0.01990501,  0.02868885, -0.0077084 , ...,  0.05345419,
         0.00370258,  0.03865541],
       [-0.00046243, -0.03486785, -0.07422936, ...,  0.02858575,
         0.01059051, -0.00720539],
       [-0.01965646, -0.0043859 , -0.00547189, ..., -0.05873794,
        -0.01624213, -0.04051956]])

In [10]:
colors = ['blue', 'orange', 'green', 'red', 'purple', 'brown', 'pink', 'gray', 'cyan', 'yellow', 'magenta', 'teal']

In [12]:
import plotly.graph_objects as go
from sklearn.cluster import KMeans
import numpy as np

# Example data (replace with your actual data)
# Symbols to use for clusters
symbols  = ['circle', 'square', 'diamond', 'cross', 'x', 'triangle-up', 'triangle-down', 'star']

# Create the figure
fig = go.Figure()

x_sampled = []
y_sampled = []


# Perform KMeans clustering and plot for each class
for class_idx in range(nb_classes):
    # Filter data for the current class
    class_data = feats_transformed[ys_ == class_idx]
    
    # Perform KMeans clustering
    kmeans = KMeans(n_clusters=5, random_state=0).fit(class_data)
    predicted_clusters = kmeans.predict(class_data)
    
    total_sampled_points_x = []
    total_sampled_point_y = []

    # Plot each cluster with a different symbol
    cluster_centers = kmeans.cluster_centers_
    
    for cluster_idx in range(len(kmeans.cluster_centers_)):
        cluster_data = class_data[predicted_clusters == cluster_idx]
        cluster_cov = np.cov(cluster_data, rowvar=False)
        cluster_mean = np.mean(cluster_data, axis=0)
        
        if(len(cluster_data)<=1):
            continue

        n_samples = (int(len(cluster_data)/len(class_data)*samples_each_class))
        ellipse_points, sampled_points = get_ellipse_points(cluster_mean, cluster_cov, n_samples=n_samples)

        total_sampled_points_x.extend(pca.inverse_transform(sampled_points))
        total_sampled_point_y.extend([class_idx]*n_samples)

        fig.add_trace(go.Scatter(
            x=cluster_data[:, 0],
            y=cluster_data[:, 1],
            mode='markers',
            marker=dict(
                symbol=symbols[cluster_idx],
                size=5,
                color= colors[class_idx]  # Same color for all clusters in a class
            ),
            name=f'Cluster {cluster_idx}'
        ))
        
        
        fig.add_trace(go.Scatter(
        x=[cluster_centers[cluster_idx][0]], y=[cluster_centers[cluster_idx][1]],
        mode='markers',
        marker=dict(symbol=symbols[cluster_idx], color=colors[class_idx], size=12, line=dict(color='black', width=2)),
        name=f"Cluster Center"
    ))
        
        
        fig.add_trace(go.Scatter(
            x=sampled_points[:, 0],
            y=sampled_points[:, 1],
            mode='markers',
            marker=dict(symbol=symbols[cluster_idx], size=6, color=colors[class_idx], opacity=0.6, line=dict(color='black', width=2)),
            name='Sampled Points'
        ))

        fig.add_trace(go.Scatter(
            x=ellipse_points[:, 0],
            y=ellipse_points[:, 1],
            mode='lines',
            line=dict(color=colors[class_idx], width=2),
            name=f'Cluster {cluster_idx} Ellipse'
        ))

    x_sampled.extend(total_sampled_points_x)
    y_sampled.extend(total_sampled_point_y)


# Update layout for better visualization
fig.update_layout(
    title="Interactive Clusters by Class",
    xaxis_title="Dimension 1",
    yaxis_title="Dimension 2",
    legend_title="Classes and Clusters",
    width=800,
    height=600,
)

# Show the plot
fig.show()


TypeError: 'NoneType' object is not subscriptable

In [38]:
pca.inverse_transform(feats_transformed)

array([[-0.00258023, -0.03179847, -0.07381665, ...,  0.0318604 ,
         0.01304789, -0.00445232],
       [ 0.00238455, -0.00774048, -0.00124356, ...,  0.00173878,
        -0.0208538 , -0.01290133],
       [ 0.00180813, -0.01040284, -0.00983361, ...,  0.00530135,
        -0.01633067, -0.01144988],
       ...,
       [ 0.00245659,  0.00094757, -0.01065572, ...,  0.00546995,
         0.01607856,  0.01696934],
       [-0.00256914, -0.03176118, -0.07363374, ...,  0.03178483,
         0.01289812, -0.0045305 ],
       [-0.00256284, -0.03194646, -0.07327094, ...,  0.03163878,
         0.01188673, -0.00531733]])

tensor([[-0.0019, -0.0366, -0.0727,  ...,  0.0298,  0.0125, -0.0038],
        [-0.0207,  0.0009, -0.0024,  ..., -0.0649, -0.0082, -0.0345],
        [-0.0192,  0.0310, -0.0054,  ...,  0.0521,  0.0026,  0.0380],
        ...,
        [ 0.0092, -0.0049, -0.0075,  ...,  0.0059,  0.0075,  0.0097],
        [-0.0010, -0.0338, -0.0733,  ...,  0.0296,  0.0123, -0.0103],
        [-0.0027, -0.0357, -0.0704,  ...,  0.0291,  0.0058, -0.0108]])

In [41]:
pca.inverse_transform(embedded_data)

array([[ 2.76767662e-02,  7.32268182e-02,  4.20664122e-01, ...,
        -1.72500274e-01, -3.80219403e-01, -2.05539466e-01],
       [ 4.11264762e-02,  6.97693217e-02,  7.03396472e-01, ...,
        -2.88405686e-01, -7.80067799e-01, -4.75277637e-01],
       [ 1.84491165e-03, -2.05955003e-02,  3.71929134e-03, ...,
        -1.05720841e-04, -6.31251636e-02, -4.88141088e-02],
       [ 5.55171859e-02,  6.01560127e-01,  3.33884757e-01, ...,
        -1.44755789e-01,  1.19532138e+00,  1.16214069e+00],
       [-1.76450783e-01, -9.26341685e-01, -2.55010719e+00, ...,
         1.06074399e+00,  9.66880502e-01,  1.04358052e-01],
       [ 4.03499492e-02,  9.64542314e-02,  6.53834455e-01, ...,
        -2.68475158e-01, -6.38119668e-01, -3.64442975e-01]])

In [42]:
criterion_pa.proxies

Parameter containing:
tensor([[-1.3944,  2.6003,  0.7679,  ...,  1.8937,  0.6779,  2.5445],
        [ 1.6610, -1.2624,  1.0693,  ...,  1.0595, -2.3948, -0.4486],
        [ 0.0684,  0.4714,  1.3393,  ..., -0.9870,  0.3520, -0.0211],
        [ 0.0798,  0.8139,  0.5623,  ..., -0.3997,  0.8228,  1.0951],
        [-0.4760, -0.5572, -2.3471,  ...,  0.5864,  0.6751,  0.1273],
        [-1.5493,  1.0870,  0.9801,  ..., -4.1079, -0.6513, -1.6170]],
       requires_grad=True)

In [11]:
tsne = TSNE(n_components=2, random_state=42)
original_len_feats = len(feats)
feats = np.concatenate((feats, np.array(x_sampled),  ))
feats_transformed = tsne.fit_transform(feats)

In [12]:
embedded_data = feats_transformed[-nb_classes:]  # Transformation of Proxy Anchors
feats_sp_transformed = feats_transformed[original_len_feats:original_len_feats+ len(x_sampled)] # Transformation of Sampled Data
feats_transformed = feats_transformed[:original_len_feats]  # Transformation of training data.

In [28]:
feats

tensor([[ 0.0085,  0.0087, -0.0060,  ...,  0.0644,  0.0029,  0.0384],
        [-0.0017, -0.0308, -0.0731,  ...,  0.0279,  0.0100, -0.0048],
        [-0.0151, -0.0077, -0.0036,  ..., -0.0556, -0.0130, -0.0411],
        ...,
        [-0.0017, -0.0343, -0.0731,  ...,  0.0251,  0.0117,  0.0014],
        [ 0.0019, -0.0344, -0.0739,  ...,  0.0293,  0.0082, -0.0041],
        [-0.0202, -0.0095,  0.0016,  ..., -0.0560, -0.0147, -0.0430]])

In [29]:
pca.inverse_transform(feats_transformed)

array([[ 0.00249744, -0.00709465,  0.00028274, ...,  0.00110321,
        -0.02118143, -0.0127382 ],
       [-0.00245386, -0.03127586, -0.07185662, ...,  0.03104877,
         0.01178197, -0.00499033],
       [ 0.00214632, -0.00891201, -0.00470436, ...,  0.00317555,
        -0.01930401, -0.01255758],
       ...,
       [-0.00256735, -0.03168827, -0.0736883 , ...,  0.03180612,
         0.01317433, -0.00430241],
       [-0.00253443, -0.03195778, -0.07266868, ...,  0.03139195,
         0.01102413, -0.00590153],
       [ 0.00220572, -0.00877679, -0.00364445, ...,  0.00273884,
        -0.02039467, -0.01320767]])

In [15]:
# Define color mapping
colors = ['blue', 'orange', 'green', 'red', 'purple', 'brown', 'pink', 'gray', 'cyan', 'yellow', 'magenta', 'teal']
Mapping = {}

if dataset == 'realworld':
    Mapping = {
        0: 'Climbing Down', 1: 'Climbing Up', 2: 'Jumping', 3: 'Lying',
        4: 'Running', 5: 'Sitting', 6: 'Standing', 7: 'Walking'
    }

# Create an interactive plot with Plotly
fig = go.Figure()

# Plot each class with interactive hover labels
for class_idx in range(nb_classes):
    class_data = feats_transformed[ys_ == class_idx]
    cluster_center = np.mean(class_data, axis=0)
    label = Mapping.get(class_idx, f'Class {class_idx}')
    
    sampled_data = feats_sp_transformed[np.array(y_sampled)==class_idx]

    # Plot each point in the class
    fig.add_trace(go.Scatter(
        x=class_data[:, 0], y=class_data[:, 1],
        mode='markers',
        marker=dict(color=colors[class_idx], size=5, opacity=0.5),
        name=label,
        text=[f"Class: {label}"] * len(class_data),
        hoverinfo='text'
    ))
    

    # Plot proxy anchor for each class
    fig.add_trace(go.Scatter(
        x=[embedded_data[class_idx][0]], y=[embedded_data[class_idx][1]],
        mode='markers',
        marker=dict(symbol='diamond', color=colors[class_idx], size=12, line=dict(color='black', width=2)),
        name=f"{label} Anchor"
    ))
    
    # Plot cluster center
    fig.add_trace(go.Scatter(
        x=[cluster_center[0]], y=[cluster_center[1]],
        mode='markers',
        marker=dict(symbol='hexagon', color=colors[class_idx], size=12, line=dict(color='black', width=2)),
        name=f"{label} Center"
    ))

    
    # Plot each point in the class from the samples indices
    fig.add_trace(go.Scatter(
        x=sampled_data[:, 0], y=sampled_data[:, 1],
        mode='markers',
        marker=dict(color=colors[class_idx], size=12, symbol = 'x', line=dict(color='black', width=2)),
        name="Sampled Data",
       
        hoverinfo='text'
    ))

    
    

# Layout adjustments for labels and aesthetics
fig.update_layout(
    title="Interactive Visualization of Proxies and Classes",
    xaxis_title="Dimension 1",
    yaxis_title="Dimension 2",
    legend_title="Classes",
    width=800,
    height=800
)

# Display the plot
fig.show()


In [42]:
sampled_data

array([[ 0.00213343, -0.00917441, -0.00464196, ...,  0.00315386,
        -0.02011314, -0.01325467],
       [ 0.00212466, -0.00964728, -0.00423003, ...,  0.00299194,
        -0.02198476, -0.01478772],
       [ 0.00220532, -0.00928203, -0.00301867, ...,  0.0024897 ,
        -0.02265071, -0.01501726],
       ...,
       [ 0.00169898, -0.01076922, -0.01163299, ...,  0.00604477,
        -0.01485604, -0.01067962],
       [ 0.00134834, -0.01337976, -0.01561474, ...,  0.00771657,
        -0.01655204, -0.01336106],
       [ 0.00147976, -0.01205613, -0.01455555, ...,  0.00726251,
        -0.01436722, -0.01111449]])

In [9]:
  # Generate synthetic features for old classes


In [10]:
# # Visualization using t-SNE (or another dimensionality reduction method)
# method = 'tsne'
# utils_CGCD.visualize_proxy_anchors(model, dlod_test_0, criterion_pa.proxies, args.dataset, args.sz_embedding, nb_classes, step, dim_reduction_method)


In [11]:
###
print('==> Evaluation of Stage 1 Dataset on Stage 1 Model')
model.eval()  # Set model to evaluation mode (disables dropout, batchnorm)
with torch.no_grad():  # Disable gradient calculation (speeds up and reduces memory usage)
    # Extract features and perform evaluation on the test dataset
    feats, _ = utils_CGCD.evaluate_cos_(model, dlod_test_0)

    # Calculate cosine similarity between normalized features and proxy anchors
    cos_sim = F.linear(losses.l2_norm(feats), losses.l2_norm(criterion_pa.proxies))  # Cosine similarity between -1 and 1

    # Get predicted labels based on maximum cosine similarity (class with highest similarity)
    _, preds_lb = torch.max(cos_sim, dim=1)
    preds = preds_lb.detach().cpu().numpy()

    # Compute accuracy and F1 score using Hungarian matching on the predictions
    # stage_1_acc_0, _ = utils_CGCD._hungarian_match_(np.array(dlod_test_0.dataset.ys), preds)
    stage_1_acc_0 = accuracy_score(np.array(dlod_test_0.dataset.ys), preds)
    stage_1_f1_0 = f1_score(np.array(dlod_test_0.dataset.ys), preds, average='macro')


    # Log results to Weights & Biases if enabled
    if args.use_wandb:
        wandb.log({"M1-TA1_Old": stage_1_acc_0})
        wandb.log({"M1-TF1_Old": stage_1_f1_0})

# Store predictions and print results for Stage 1
preds1 = preds
print(f"Stage 1 {len(preds)}, Unique {np.unique(np.array(dlod_test_0.dataset.ys))}")
print("Step 1 Test Dataset Accuracy on Stage 1 trained Model", stage_1_acc_0)
print("Step 1 Test Dataset F1 Score on Stage 1 trained Model", stage_1_f1_0)

# Write results to log file
# with open(pth_rst_exp_log_step_1, "a") as file:
#     file.write(f"Step 1: Test Dataset Acc: {stage_1_acc_0} F1: {stage_1_f1_0}\n")
if(args.log_results ):    logger_1.info(f"Step 1: Test Dataset Acc: {stage_1_acc_0} F1: {stage_1_f1_0}\n")

# Append Stage 1 results for future reference
stage_1_test_accs_seen.append(stage_1_acc_0)
stage_1_test_f1s_seen.append(stage_1_f1_0)

==> Evaluation of Stage 1 Dataset on Stage 1 Model
Stage 1 19854, Unique [0 1 2 3 4 5]
Step 1 Test Dataset Accuracy on Stage 1 trained Model 0.6968872771229979
Step 1 Test Dataset F1 Score on Stage 1 trained Model 0.7337358693389304


In [12]:

# Prepare data for Stage 2 training
dlod_tr_prv = dlod_tr_0
dset_tr_now_md = 'train_1'  # Set mode for Stage 2 training dataset
dset_ev_now_md = 'eval_1'  # Set mode for Stage 2 evaluation dataset
nb_classes_prv = nb_classes  # Keep track of number of classes seen in Stage 1


# exit()
# Load the new training and evaluation datasets for Stage 2
dset_tr_now = dataset.load(name=args.dataset, root=pth_dataset, mode=dset_tr_now_md, windowlen=window_len, autoencoderType=None, standardize=args.standarization_prerun, fold=fold)


# If contrastive loss is 'Offline', extend current dataset with Stage 1 dset_tr_now
if args.contrastive_loss_type in ['Offline', 'Offline_NCE']:
    print("Adding Stage 1 Training Data to the Stage 2 Training Data For Offline Model..")
    dset_tr_now.xs.extend(dset_tr_0.xs)
    dset_tr_now.ys.extend(dset_tr_0.ys)
    dset_tr_now.I.extend(dset_tr_0.I)

# Standardize training data
mean = np.mean(dset_tr_now.xs, axis=0)
std = np.std(dset_tr_now.xs, axis=0)
if(args.standarization_run_time): dset_tr_now.xs = (dset_tr_now.xs - mean) / (std + 1e-5)

# Standardize evaluation and test datasets using same mean and std from training data
dset_ev_now = dataset.load(name=args.dataset, root=pth_dataset, mode=dset_ev_now_md, windowlen=window_len, autoencoderType=None, standardize=args.standarization_prerun, fold=fold)
if(args.standarization_run_time): dset_ev_now.xs = (dset_ev_now.xs - mean) / (std + 1e-5)
dset_test = dataset.load(name=args.dataset, root=pth_dataset, mode='test_1', windowlen=window_len, autoencoderType=None, standardize=args.standarization_prerun, fold=fold)
if(args.standarization_run_time): dset_test.xs = (dset_test.xs - mean) / (std + 1e-5)



# Create data loaders for the newly loaded datasets
dlod_tr_now = torch.utils.data.DataLoader(dset_tr_now, batch_size=args.sz_batch, shuffle=True, num_workers=args.nb_workers, pin_memory=True, worker_init_fn=lambda x: np.random.seed(42))
dlod_ev_now = torch.utils.data.DataLoader(dset_ev_now, batch_size=args.sz_batch, shuffle=False, num_workers=args.nb_workers, pin_memory=True, worker_init_fn=lambda x: np.random.seed(42))
dlod_test = torch.utils.data.DataLoader(dset_test, batch_size=args.sz_batch, shuffle=False, num_workers=args.nb_workers, pin_memory=True, worker_init_fn=lambda x: np.random.seed(42))

print("Incremental Step \n")
dset_tr_now.nb_classes()
nb_subjects = dset_tr_now.nb_subjects()
print("\n")

# Evaluate Stage 2 test dataset on Stage 1 trained model
print('==> Evaluation of Stage 2 Dataset on Stage 1 Model')
model.eval()  # Set model to evaluation mode
with torch.no_grad():
    # Extract features from the test data
    feats, _ = utils_CGCD.evaluate_cos_(model, dlod_test)
    
    # Compute cosine similarity between features and proxy anchors
    cos_sim = F.linear(losses.l2_norm(feats), losses.l2_norm(criterion_pa.proxies))
    _, preds_lb = torch.max(cos_sim, dim=1)
    preds = preds_lb.detach().cpu().numpy()

    # Split predictions into old (Stage 1) and new (Stage 2) classes
    y_temp = torch.tensor(dlod_test.dataset.ys)

    old_classes = np.nonzero(torch.where(y_temp < nb_classes, 1, 0))
    new_classes = np.nonzero(torch.where(y_temp >= nb_classes, 1, 0))

    # Compute accuracy and F1 score for old and new classes separately
    # print(old_classes)
    # print(np.array(dlod_test.dataset.ys)[old_classes].shape)
    # print(preds[old_classes].)

    stage_2_acc_0 = accuracy_score(np.array(dlod_test.dataset.ys)[old_classes].reshape(-1), preds[old_classes].reshape(-1))
    stage_2_acc_1 = accuracy_score(np.array(dlod_test.dataset.ys)[new_classes].reshape(-1), preds[new_classes].reshape(-1))
    stage_2_f1_0 = f1_score(np.array(dlod_test.dataset.ys)[old_classes].reshape(-1), preds[old_classes].reshape(-1), average='macro')


# Print the Stage 2 accuracy results
print("Stage 2 Test Dataset on Stage 1 trained model, Seen Accuracy {:.4f}  Unseen Accuracy  {:.4f}".format(stage_2_acc_0, stage_2_acc_1))


# Log results to a file
# with open(pth_rst_exp_log_step_1, "a") as file:
#     file.write(f"Stage 2: Test Dataset Acc Seen Acc: {stage_2_acc_0}, Seen F1: {stage_2_f1_0} Unseen Acc: {stage_2_acc_1} \n")
if(args.log_results):    logger_1.info(f"Stage 2: Test Dataset Acc Seen Acc: {stage_2_acc_0}, Seen F1: {stage_2_f1_0} Unseen Acc: {stage_2_acc_1} \n")
# Log Stage 2 results to Weights & Biases if enabled
if args.use_wandb:
    wandb.log({"M1-TA2_Old": stage_2_acc_0})  # Stage 2 test accuracy (seen classes)
    wandb.log({"M1-TF2_Old": stage_2_f1_0})  # Stage 2 test F1 score (seen classes)

# Append Stage 2 results to the lists for future reference
stage_2_test_accs_seen.append(stage_2_acc_0)
stage_2_test_f1s_seen.append(stage_2_f1_0)

####
# If we're not just testing on step 2, proceed with training
if args.only_test_step2 != True:
    load_exempler = False
    if load_exempler:
        # Load saved exemplar data for the model
        print("Loading Saved Exempler ..")
        expler_s = torch.load(pth_rst_exp_step_1 + 'expler_s_tensor_model_{}_{}_windowlen_{}_sz_embedding_{}_alpha{}_mrg_{}_PA_{}_KD_{}_lr_{}_wd_{}_fold_{}.pt'.format(args.dataset, args.model, window_len, args.sz_embedding, args.alpha, args.mrg, args.pa_weight, args.kd_weight, args.lr, args.weight_decay, fold), map_location=torch.device(device))
    else:
        # Calculate exemplar statistics (mean and standard deviation) for the proxies
        print('==> Calc. proxy mean and sigma for exemplar..')
        with torch.no_grad():
            feats, _ = utils_CGCD.evaluate_cos_(model, dlod_tr_prv)
            feats = losses.l2_norm(feats)
            # print(feats.shape)
            expler_s = feats.std(dim=0).to(device)

            torch.save(expler_s, pth_rst_exp_step_1 + 'expler_s_tensor_model_{}_{}_windowlen_{}_sz_embedding_{}_alpha{}_mrg_{}_PA_{}_KD_{}_lr_{}_wd_{}_fold_{}.pt'.format(args.dataset, args.model, window_len, args.sz_embedding, args.alpha, args.mrg, args.pa_weight, args.kd_weight, args.lr, args.weight_decay, fold))


Incremental Step 

Classes:  {np.int64(0), np.int64(1), np.int64(2), np.int64(3), np.int64(4), np.int64(5), np.int64(6), np.int64(7)}
Subjects:  {np.str_('imu\\2'), np.str_('imu\\7'), np.str_('imu\\9'), np.str_('imu\\3'), np.str_('imu\\8'), np.str_('imu\\5')}


==> Evaluation of Stage 2 Dataset on Stage 1 Model
Stage 2 Test Dataset on Stage 1 trained model, Seen Accuracy 0.6969  Unseen Accuracy  0.0000


In [13]:

                        ################################  Incremental Step ########################################
                    ##########################################        ################################################################


# Update number of classes for current training phase and initialize the proxy-anchor loss
nb_classes_now = dset_tr_now.nb_classes()
criterion_pa_now = losses.Proxy_Anchor(nb_classes=nb_classes_now, sz_embed=args.sz_embedding, mrg=args.mrg, alpha=args.alpha).to(device)
criterion_pa_now.proxies.data[:nb_classes_prv] = criterion_pa.proxies.data  # Reuse proxies from Stage 1
criterion_pa.proxies.requires_grad = False

# Initialize best performance metrics for tracking
bst_acc_a, bst_acc_oo, bst_acc_on, bst_acc_no, bst_acc_nn = 0., 0., 0., 0., 0.
bst_epoch_a, bst_epoch_o, bst_epoch_n = 0., 0., 0.

# Create a deep copy of the model for Stage 2 training

model_now = copy.deepcopy(model)
model_now = model_now.to(device)

# Set up different learning rates for different parts of the model
if args.model == 'tinyhar':
    param_groups = [
        {'params': list(set(model_now.model.parameters()).difference(set(model_now.model.prediction.parameters()))) if gpu_id != -1 else list(set(model_now.module.parameters()).difference(set(model_now.module.model.prediction.parameters())))},
        {'params': model_now.model.prediction.parameters() if gpu_id != -1 else model_now.model.prediction.parameters(), 'lr': float(args.lr) * 1},
    ]
else:
    param_groups = [
        {'params': list(set(model_now.parameters()).difference(set(model_now.embedding.parameters()))) if gpu_id != -1 else list(set(model_now.module.parameters()).difference(set(model_now.module.model.embedding.parameters())))},
        {'params': model_now.embedding.parameters() if gpu_id != -1 else model_now.embedding.parameters(), 'lr': float(args.lr) * 1},
    ]

# Add proxy-anchor parameters to optimizer with a higher learning rate
param_groups.append({'params': criterion_pa_now.parameters(), 'lr': float(args.lr) * 100})

# Initialize the optimizer (AdamW) with the specified parameter groups
opt = torch.optim.AdamW(param_groups, lr=float(args.lr), weight_decay=args.weight_decay, betas=(0.9, 0.999))

# scheduler = torch.optim.lr_scheduler.StepLR(opt, step_size=args.lr_decay_step, gamma=args.lr_decay_gamma)

# Scheduler is currently commented out. If used, it would adjust the learning rate at specified intervals.
# scheduler = torch.optim.lr_scheduler.StepLR(opt, step_size=args.lr_decay_step, gamma=args.lr_decay_gamma)

print("Classes in the initial Step: {}, Incremental Step: {}".format(nb_classes, nb_classes_now))
if args.use_wandb:
    wandb.log({"M1 Classes": nb_classes})
    wandb.log({"M2 Classes": nb_classes_now})

# Training the Incremental Step
# If loss weights are learnable, initialize them as tensors with requires_grad=True.
if args.learnable_loss_weights:
    args.pa_weight = torch.tensor(1.0, requires_grad=True)
    args.kd_weight = torch.tensor(1.0, requires_grad=True)
    args.contrastive_weight = torch.tensor(1.0, requires_grad=True)

epoch = 0
best_weighted_acc = 0
es_count = 0
step = 2
ep = args.nb_epochs

if(args.only_test_step2 == False):
    first_validation_losses= losses.get_validation_losses_step_2(model, model_now, criterion_pa, criterion_pa_now, expler_s, nb_classes_prv, nb_classes_now, args, nce_loss, dlod_ev_now)
    validation_losses  = first_validation_losses
# Training loop for the incremental step
for epoch in range(0, args.nb_epochs):
    if args.only_test_step2:
        continue  # Skip training if only testing step 2

    model_now.train()  # Set the model to training mode

    # Freeze BatchNorm layers if bn_freeze is enabled
    if args.bn_freeze:
        modules = model_now.modules() if args.gpu_id != -1 else model_now.module.model.modules()
        for m in modules:
            if isinstance(m, nn.BatchNorm2d):
                m.eval()

    # Handle warm-up phase
    if args.warm > 0:
        if args.gpu_id != -1:
            if args.model == 'tinyhar':
                unfreeze_model_param = list(model_now.model.prediction.parameters()) + list(criterion_pa_now.parameters())
            else:
                unfreeze_model_param = list(model_now.embedding.parameters()) + list(criterion_pa_now.parameters())
        else:
            if args.model == 'tinyhar':
                unfreeze_model_param = list(model_now.model.prediction.parameters()) + list(criterion_pa_now.parameters())
            else:
                unfreeze_model_param = list(model_now.embedding.parameters()) + list(criterion_pa_now.parameters())

        if epoch == 0:
            for param in list(set(model_now.parameters()).difference(set(unfreeze_model_param))):
                param.requires_grad = False
        if epoch == args.warm:
            for param in list(set(model_now.parameters()).difference(set(unfreeze_model_param))):
                param.requires_grad = True

    # Iterate over the training data
    pbar = tqdm(enumerate(dlod_tr_now))
    total_train_loss, total_kd_loss, total_pa_loss, total_contrastive_loss = 0.0, 0.0, 0.0, 0.0
    total_data = 0
    for batch_idx, (x, y, z) in pbar:
        feats = model_now(x.squeeze().to(device))
        y_batch = y
        y_n = torch.where(y >= nb_classes_prv, 1, 0)  # Identify new classes
        # Feature replay is not used in Online Finetuning and Offline Model, G-Basleline_Without_Feature_Replay
        if args.contrastive_loss_type not in  ["Online_Finetuning", 'Offline', 'Online_Finetuning_NCE', 'Offline_NCE', 'G-Baseline_NCE_WFR']:
            # Example replay: Generate old class examples to mitigate forgetting

            y_o = y.size(0) - y_n.sum()  # Count old classes
            
            if y_o > 0:
                y_sp = torch.randint(nb_classes_prv, (500,))  # Randomly select old class proxies
                feats_sp = torch.normal(criterion_pa.proxies[y_sp], expler_s).to(device)  # Generate synthetic features for old classes
                y = torch.cat((y, y_sp), dim=0)
                feats = torch.cat((feats, feats_sp), dim=0)
                
        # Compute Proxy-Attention loss
        loss_pa = criterion_pa_now(feats, y.squeeze().to(device))

        # # Compute Knowledge Distillation (KD) loss
        # feats_new = model_now(x.squeeze().to(device))
        # logits_new = F.linear(losses.l2_norm(feats_new), losses.l2_norm(criterion_pa_now.proxies))[:, :nb_classes_prv]
        # with torch.no_grad():
        #     feats_old = model(x.squeeze().to(device))
        #     logits_old = F.linear(losses.l2_norm(feats_old), losses.l2_norm(criterion_pa.proxies))
        # T = 2  # Temperature for softening the probability distributions
        # p = F.log_softmax(logits_new / T, dim=1)
        # q = F.softmax(logits_old / T, dim=1)
        # loss_kd = F.kl_div(p, q, size_average=False) * (T**2) / y.shape[0]

        ### KD
        # We perform no knowledge distillattion for Online and Offline Models.
        if args.contrastive_loss_type not in  ["Online_Finetuning", 'Offline', 'Online_Finetuning_NCE', 'Offline_NCE']:
            # y_n = torch.where(y_batch >= nb_classes_prv, 0, 1) # Remove it
            y_o_msk = torch.nonzero(y_n)  # Provides index of all new classes

            # if y_o_msk.size(0) > 1:
            #     y_o_msk = torch.nonzero(y_n).squeeze()
            #     x_o = torch.unsqueeze(x[y_o_msk[0]], dim=0)  # Just first element

            #     feats_n = torch.unsqueeze(feats[y_o_msk[0]], dim=0)
            #     for kd_idx in range(1, y_o_msk.size(0)): # After 1st Index
            #         try:    
            #             x_o_ = torch.unsqueeze(x[y_o_msk[kd_idx]], dim=0)
            #         except:
            #             raise ValueError("A value error occurred",kd_idx , y_o_msk[kd_idx])

            #         x_o = torch.cat((x_o, x_o_), dim=0)
            #         feats_n_ = torch.unsqueeze(feats[y_o_msk[kd_idx]], dim=0)
            #         feats_n = torch.cat((feats_n, feats_n_), dim=0)
            #     with torch.no_grad():
            #         feats_o = model(x_o.squeeze().to(device))
            #     feats_n = feats_n.to(device)
            #     # FRoST
            #     loss_kd = torch.dist(F.normalize(feats_o.view(feats_o.size(0) * feats_o.size(1), 1), dim=0).detach(), F.normalize(feats_n.view(feats_o.size(0) * feats_o.size(1), 1), dim=0))
            # else:
            #     loss_kd = torch.tensor(0.).to(device)
            loss_kd = (criterion_pa.proxies - criterion_pa_now.proxies[0:nb_classes]).pow(2).sum(1).sqrt().sum().to(device)
        else:
            loss_kd = torch.tensor(0.).to(device)
            # model_now.kd_weight_lr.requires_grad  = False
        
        

        # Compute INFO_NCE Contrastive Loss
        # Offline_NCE and Online_Finetuning_NCE have contrastive loss
        if args.contrastive_loss_type in ['G-Baseline_NCE', 'Offline_NCE', 'Online_Finetuning_NCE', 'G-Baseline_NCE_WFR']:
            positive_proxies = criterion_pa_now.proxies[[torch.tensor(y, dtype=torch.long)]]
            negative_proxies = []
            for y_temp in y:
                t = [i for i in range(nb_classes_now) if i != y_temp.item()]

                #If else is just to append the data int the array
                if len(negative_proxies) == 0:
                    negative_proxies = criterion_pa_now.proxies[t].unsqueeze(0)
                else:
                    negative_proxies = torch.concat((negative_proxies, criterion_pa_now.proxies[t].unsqueeze(0)))

            contrastive_loss = nce_loss(feats, positive_proxies, negative_proxies)

        # Computer Simple Contrastive Loss
        elif args.contrastive_loss_type == 'G-Baseline_Contrastive':
            contrastive_loss = utils_CGCD.contrastive_loss(feats, y, criterion_pa.proxies, True).to(device)
        else:
            contrastive_loss = torch.tensor(0).to(device)
            # model_now.contrastive_weight_lr.requires_grad  = False

        training_losses = [loss_pa, loss_kd, contrastive_loss]
        losses_ind = []
        # Getting Losses indices which are not zero
        for i in range(3):
            if(validation_losses[i]!=0 and training_losses[i].item()!=0):      losses_ind.append(i)

        # Getting the selected training and validation losses
        training_losses = [training_losses[i] for i in losses_ind]
        validation_losses_t = [validation_losses[i] for i in losses_ind]

        # Getting the initial validation losses calculated before training on selected indices
        first_validation_losses_t = [first_validation_losses[i] for i in losses_ind]

        # Calculating Max Ration
        max_ratio = max([validation_losses_t[i] / training_losses[i].item() for i in range(len(validation_losses_t))])
        
        # Calculating Weights for each valid loss
        weights = [(validation_losses_t[i] / training_losses[i].item()) / first_validation_losses_t[i] for i in range(len(validation_losses_t))]

        # Normalizing the Weights
        normalized_weights = [weights[i] / min(weights) for i in range(len(weights))]
        # Compute the total losspint

        # Adding Weighted loss in the final loss.
        loss = 0
        for i in range(len(validation_losses_t)): loss += weights[i]*training_losses[i]




        total_train_loss += loss.item() * x.size(0)
        total_kd_loss += loss_kd.item() * x.size(0)
        total_pa_loss += loss_pa.item() * x.size(0)
        total_contrastive_loss += contrastive_loss.item() * x.size(0)
        total_data += x.size(0)

        opt.zero_grad()
        loss.backward()
        opt.step()

        pbar.set_description('Train Epoch: {} [{}/{} ({:.0f}%)] Loss: {:.6f}/{:.6f}/{:.6f}'.format(
            epoch, batch_idx + 1, len(dlod_tr_now), 100. * batch_idx / len(dlod_tr_now),
            loss.item(), loss_pa.item(), loss_kd.item()
        ))

    if total_data > 0:
        print("Epoch {} Train Total Loss {:.4f}, PA Loss {:.4f}, KD Loss {:.4f} Contrastive Loss {:.4f}".format(
            epoch, total_train_loss / total_data, total_pa_loss / total_data, 
            total_kd_loss / total_data, total_contrastive_loss / total_data
        ))

    if args.use_wandb:
        wandb.log({"Step 2: Train Loss": total_train_loss / total_data, "Step 2: Train PA Loss": total_pa_loss / total_data, 
                "Step 2: Train KD Loss": total_kd_loss / total_data, "Step 2: Train Contrastive Loss": total_contrastive_loss / total_data, 
                "custom_step": epoch})

    # The scheduler step is commented out. If used, it would adjust the learning rate based on the scheduler's policy.
    # scheduler.step()


    ####
    # Begin the evaluation phase
    print('==> Evaluation..')
    model_now.eval()  # Set the model to evaluation mode
    validation_losses  = losses.get_validation_losses_step_2(model, model_now, criterion_pa, criterion_pa_now, expler_s,
                                        nb_classes_prv, nb_classes_now, args, nce_loss, dlod_ev)
    with torch.no_grad():  # Disable gradient calculation for evaluation
        # Evaluate the model on the validation dataset
        feats, _ = utils_CGCD.evaluate_cos_(model_now, dlod_ev_now)
        cos_sim = F.linear(losses.l2_norm(feats), losses.l2_norm(criterion_pa_now.proxies))
        _, preds_lb = torch.max(cos_sim, dim=1)  # Get predicted labels

        y = torch.tensor(dlod_ev_now.dataset.ys).type(torch.LongTensor)  # Ground truth labels

        # Identify seen and unseen classes
        seen_classes = torch.where(y < nb_classes, 1, 0)
        seen_classes_idx = torch.nonzero(seen_classes)
        unseen_classes = torch.where(y >= nb_classes, 1, 0)
        unseen_classes_idx = torch.nonzero(unseen_classes)

        # Calculate accuracy for seen classes
        if seen_classes.sum().item() > 0:
            acc_o = calculate_accuracy(y[seen_classes_idx].to(device), preds_lb[seen_classes_idx].to(device))
        else:
            acc_o = 0

        # Calculate accuracy for unseen classes
        if unseen_classes.sum().item() > 0:
            acc_n = calculate_accuracy(y[unseen_classes_idx].to(device), preds_lb[unseen_classes_idx].to(device))
        else:
            acc_n = 0

        # Calculate overall accuracy
        acc_a = calculate_accuracy(y.to(device), preds_lb.to(device))

        # Logging validation results
        print("Valid Accuracies Seen {:.2f}, Unseen {:.2f}, Overall {:.2f}".format(acc_o, acc_n, acc_a))
        if args.use_wandb:
            wandb.log({"Step 2: Validation Seen Acc": acc_o, "custom_step": epoch})
            wandb.log({"Step 2: Validation Unseen Acc": acc_n, "custom_step": epoch})
            wandb.log({"Step 2: Validation Overall Acc": acc_a, "custom_step": epoch})

    # Update best metrics and save the model if the current model performs better
    if (acc_o + acc_n + acc_a) / 3 > best_weighted_acc:
        best_seen = acc_o
        best_unseen = acc_n
        best_overall = acc_a
        best_epoch = epoch
        best_weighted_acc = (best_seen + best_unseen + best_overall) / 3
        es_count = 0
        print("Got Better Model with Seen {:.4f}, Unseen Accuracies {:.4f}, Overall {:.4f} and Average as {:.4f}".format(best_seen, best_unseen, best_overall, best_weighted_acc))
        torch.save({'model_pa_state_dict': model_now.state_dict(), 'proxies_param': criterion_pa_now.proxies},
                    '{}{}_{}_model_best_windowlen_{}_sz_embedding_{}_alpha_{}_mrg_{}_lr_{}_wd_{}_step_{}_fold_{}.pth'.format(
                        pth_rst_exp_step_2, args.dataset, args.model, window_len, args.sz_embedding,
                        args.alpha, args.mrg,  args.lr, args.weight_decay,
                        str(step), fold))
    else:
        es_count += 1
        print("Early Stopping Count ", es_count)

    # Handle early stopping based on count or epoch
    if epoch < args.warm:
        es_count = 0  # Reset early stopping counter during warm-up

    if es_count == 10 or epoch == args.nb_epochs - 1:
        # Save best results and stop if early stopping criteria are met
        # with open(pth_rst_exp_log_step_2, "a+") as fval:
        #     fval.write('Best Valid Accuracies Seen {:.4f}, Unseen {:.4f}, Overall {:.4f}, Average {:.4f}\n'.format(
        #         best_seen, best_unseen, best_overall, best_weighted_acc))
        if(args.log_results):
            logger_2.info('Best Valid Accuracies Seen {:.4f}, Unseen {:.4f}, Overall {:.4f}, Average {:.4f}\n'.format(
                    best_seen, best_unseen, best_overall, best_weighted_acc))
        stage_2_val_accs_seen.append(best_seen)
        stage_2_val_accs_unseen.append(best_unseen)
        stage_2_val_accs_overall.append(best_overall)

        print("Best Valid Accuracies Seen {:.4f}, and Unseen {:.4f}, Overall {:.4f}, Average {:.4f}".format(
            best_seen, best_unseen, best_overall, best_weighted_acc))
        print("Early Stopping")
        if args.use_wandb:
            wandb.log({"Step 2: Validation Best Seen Acc": best_seen})
            wandb.log({"Step 2: Validation Best Unseen Acc": best_unseen})
            wandb.log({"Step 2: Validation Best Overall Acc": best_overall})
        break





Classes:  {np.int64(0), np.int64(1), np.int64(2), np.int64(3), np.int64(4), np.int64(5), np.int64(6), np.int64(7)}
Classes in the initial Step: 6, Incremental Step: 8


In [14]:
# Prepare for testing the final model
pth_pth_test = '{}{}_{}_model_best_windowlen_{}_sz_embedding_{}_alpha_{}_mrg_{}_lr_{}_wd_{}_step_{}_fold_{}.pth'.format(
    pth_rst_exp_step_2, args.dataset, args.model, window_len, args.sz_embedding,
    args.alpha, args.mrg, args.lr, args.weight_decay, str(step), fold)

# Define the configuration for testing
cfg_test = {'weights_path': 'CGCD-main/src/Saved_Models/UK_BioBank_pretrained/mtl_best.mdl', "use_ssl_weights": False, 'conv_freeze': False, 'load_finetuned_mtl': False,
    'checkpoint_name': '', 'epoch_len': 2, 'output_size': '', 'embedding_dim': args.sz_embedding, 'bottleneck_dim': None,
    'output_size': nb_classes_now, 'weight_norm_dim': '', 'n_channels': n_channels, 'window_len': window_len}

# Initialize the criterion for testing
criterion_pa_test = losses.Proxy_Anchor(nb_classes=nb_classes_now, sz_embed=args.sz_embedding, mrg=args.mrg, alpha=args.alpha).to(device)

# Load the model for testing based on the configuration
if args.model == 'resnet18':
    cfg = {'weights_path': 'CGCD-main/src/Saved_Models/UK_BioBank_pretrained/mtl_best.mdl', "use_ssl_weights": False, 'conv_freeze': False, 'load_finetuned_mtl': False,
        'checkpoint_name': '', 'epoch_len': 2, 'output_size': '', 'embedding_dim': args.sz_embedding, 'bottleneck_dim': None,
        'output_size': nb_classes, 'weight_norm_dim': '', 'n_channels': n_channels, 'window_len': window_len}
    model_test = ModelGen_new(cfg_test).create_model().to(device)
elif args.model == 'tinyhar':
    model_test = tinyhar(n_channels, window_len, args.sz_embedding).to(device)
elif args.model == 'harnet':
    repo = 'OxWearables/ssl-wearables'
    model_test = torch.hub.load(repo, 'harnet5', class_num=nb_classes, pretrained=True).to(device)
    del model.classifier
    model.embedding = nn.Sequential(nn.Linear(model.feature_extractor.layer5[0].out_channels, args.sz_embedding)).to(device)

# Load the best model weights and proxies for testing
checkpoint_test = torch.load(pth_pth_test, map_location=torch.device(device))
model_test.load_state_dict(checkpoint_test['model_pa_state_dict'])
criterion_pa_test.proxies = checkpoint_test['proxies_param']

print("Testing Step \n")
dset_test.nb_classes()
nb_subjects = dset_test.nb_subjects()
print("\n")

# Perform testing
model_test.eval()
with torch.no_grad():
    feats, _ = utils_CGCD.evaluate_cos_(model_test, dlod_test)
    cos_sim = F.linear(losses.l2_norm(feats), losses.l2_norm(criterion_pa_test.proxies))
    _, preds_lb = torch.max(cos_sim, dim=1)  # Get predicted labels

    y = torch.tensor(dlod_test.dataset.ys).type(torch.LongTensor)  # Ground truth labels

    
    # Identify seen and unseen classes
    seen_classes = torch.where(y < nb_classes, 1, 0)
    seen_classes_idx = torch.nonzero(seen_classes)
    unseen_classes = torch.where(y >= nb_classes, 1, 0)
    unseen_classes_idx = torch.nonzero(unseen_classes)

    # Calculate accuracy and F1 score for seen classes
    if seen_classes.sum().item() > 0:
        acc_o = calculate_accuracy(y[seen_classes_idx].to(device), preds_lb[seen_classes_idx].to(device))
        # f1_o = f1_score(y[seen_classes_idx].to('cpu').detach().numpy(), preds_lb[seen_classes_idx].to('cpu').detach().numpy(), average='macro')
        # f1_o = np.mean(f1_score(y[seen_classes_idx].to('cpu').detach().numpy(), preds_lb[seen_classes_idx].to('cpu').detach().numpy(), average=None)[:nb_classes_prv])

    else:
        acc_o, f1_o = 0, 0

    # Calculate accuracy and F1 score for unseen classes

    if unseen_classes.sum().item() > 0:
        acc_n = calculate_accuracy(y[unseen_classes_idx].to(device), preds_lb[unseen_classes_idx].to(device))
        # f1_n = f1_score(y[unseen_classes_idx].to('cpu').detach().numpy(), preds_lb[unseen_classes_idx].to('cpu').detach().numpy(), average='macro')
        # Taking the last n classes in the confusion matrix.
        # f1_n  = np.mean(f1_score(y[unseen_classes_idx].to('cpu').detach().numpy(),
        #                  preds_lb[unseen_classes_idx].to('cpu').detach().numpy(), average=None)[-(nb_classes_now -nb_classes_prv):])


    else:
        acc_n, f1_n = 0, 0

    # Calculate overall accuracy and F1 scoreprint(f1_score(y.to('cpu').detach().numpy(), preds_lb.to('cpu').detach().numpy(), average=None))
    f1_o = np.mean(f1_score(y.to('cpu').detach().numpy(), preds_lb.to('cpu').detach().numpy(), average=None)[:nb_classes_prv])
    f1_n = np.mean(f1_score(y.to('cpu').detach().numpy(), preds_lb.to('cpu').detach().numpy(), average=None)[nb_classes_prv:])

    acc_all = calculate_accuracy(y.to(device), preds_lb.to(device))

    f1_all = f1_score(y.to('cpu').detach().numpy(), preds_lb.to('cpu').detach().numpy(), average='macro')

    # Logging test results
    print("Test Accuracies Seen {:.2f}, Unseen {:.2f}, Overall {:.2f}".format(acc_o, acc_n, acc_all))
    print("Test F1 Scores Seen {:.2f}, Unseen {:.2f}, Overall {:.2f}".format(f1_o, f1_n, f1_all))

    # print(f1_score(y.to('cpu').detach().numpy(), preds_lb.to('cpu').detach().numpy(), average = None))
    # # from sklearn.metrics import confusion_matrix
    # cm = confusion_matrix(y.to('cpu').detach().numpy(), preds_lb.to('cpu').detach().numpy())
    # # print(cm)
    # cmn = cm.astype('float') / cm.sum(axis=1)[:, np.newaxis]
    # print(np.array2string(cmn.astype('float'), formatter={'float_kind': lambda x: f"{x:.2f}"}))
    # # print(cmn)
    # # exit()
    

    test_accs_seen.append(acc_o)
    test_accs_unseen.append(acc_n)
    test_accs_overall.append(acc_all)

    test_f1s_seen.append(f1_o)
    test_f1s_unseen.append(f1_n)
    test_f1s_overall.append(f1_all)

    if args.use_wandb:
        wandb.log({"Test Seen Acc": acc_o})
        wandb.log({"Test Unseen Acc": acc_n})
        wandb.log({"Test Overall Acc": acc_all})
        wandb.log({"Test Seen F1": f1_o})
        wandb.log({"Test Unseen F1": f1_n})
        wandb.log({"Test Overall F1": f1_all})

    # Save test results to file
    # with open(pth_rst_exp_log_step_2, "a+") as fval:
    #     fval.write('Test Accuracies Seen {:.4f}, Unseen {:.4f}, Overall {:.4f}\n'.format(acc_o, acc_n, acc_all))
    #     fval.write('Test F1 Scores Seen {:.4f}, Unseen {:.4f}, Overall {:.4f}\n'.format(f1_o, f1_n, f1_all))
    if(args.log_results):
        logger_2.info('Test Accuracies Seen {:.4f}, Unseen {:.4f}, Overall {:.4f}\n'.format(acc_o, acc_n, acc_all))
        logger_2.info('Test F1 Scores Seen {:.4f}, Unseen {:.4f}, Overall {:.4f}\n'.format(f1_o, f1_n, f1_all))


if torch.cuda.is_available():
    torch.cuda.empty_cache()
del model_now
del model
del opt
del opt_pa
del criterion_pa
del criterion_pa_now




Testing Step 

Classes:  {np.int64(0), np.int64(1), np.int64(2), np.int64(3), np.int64(4), np.int64(5), np.int64(6), np.int64(7)}
Subjects:  {np.str_('imu\\4'), np.str_('imu\\1'), np.str_('imu\\6')}




/tmp/ipykernel_3761641/1763504777.py:29: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint_test = torch.load(pth_pth_test, map_location=torch.device(device))


Test Accuracies Seen 0.56, Unseen 0.59, Overall 0.57
Test F1 Scores Seen 0.65, Unseen 0.50, Overall 0.61


In [15]:
log_content = (
"XXXXXXXXXXXXXXXXXXXXXXXXXX Results Summary XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX\n"
f"Initial Stage ALL Acc Mean: {np.mean(stage_1_test_accs_seen)} Std: {np.std(stage_1_test_accs_seen)} "
f"F1 Mean: {np.mean(stage_1_test_f1s_seen)} Std: {np.std(stage_1_test_f1s_seen)}\n"

f"Before CL Seen Acc Mean: {np.mean(stage_2_test_accs_seen)} Std: {np.std(stage_2_test_accs_seen)} "
f"F1 Mean: {np.mean(stage_2_test_f1s_seen)} Std: {np.std(stage_2_test_f1s_seen)}\n"

f"After CL Seen Acc Mean: {np.mean(test_accs_seen)} Std: {np.std(test_accs_seen)} "
f"F1 Mean: {np.mean(test_f1s_seen)} Std: {np.std(test_f1s_seen)}\n"

f"After CL Unseen Acc Mean: {np.mean(test_accs_unseen)} Std: {np.std(test_accs_unseen)} "
f"F1 Mean: {np.mean(test_f1s_unseen)} Std: {np.std(test_f1s_unseen)}\n"

f"After CL Overall Acc Mean: {np.mean(test_accs_overall)} Std: {np.std(test_accs_overall)} "
f"F1 Mean: {np.mean(test_f1s_overall)} Std: {np.std(test_f1s_overall)}\n"
"XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX\n"
)
if(args.log_results):
    logger_1.info(log_content)
    logger_2.info(log_content)

In [31]:

import numpy as np
from sklearn.decomposition import PCA
from sklearn.datasets import load_iris

# Load dataset
data = load_iris()
X = data.data  # Feature matrix

# Apply PCA with fewer components
pca = PCA(n_components=2)  # Reduce to 2 components
X_pca = pca.fit_transform(X)

# Reconstruct the data using inverse transformation
X_reconstructed = pca.inverse_transform(X_pca)

# Compare original and reconstructed data
print("Original Data (first 5 rows):")
print(X[:5])
print("\nReconstructed Data (first 5 rows):")
print(X_reconstructed[:5])

Original Data (first 5 rows):
[[5.1 3.5 1.4 0.2]
 [4.9 3.  1.4 0.2]
 [4.7 3.2 1.3 0.2]
 [4.6 3.1 1.5 0.2]
 [5.  3.6 1.4 0.2]]

Reconstructed Data (first 5 rows):
[[5.08303897 3.51741393 1.40321372 0.21353169]
 [4.7462619  3.15749994 1.46356177 0.24024592]
 [4.70411871 3.1956816  1.30821697 0.17518015]
 [4.6422117  3.05696697 1.46132981 0.23973218]
 [5.07175511 3.52655486 1.36373845 0.19699991]]
